<h1 style="text-align:center; color:blue;">Fitting the model using mgcv in python</h1>

Here I will demonstrate how to use rpy2 to run R in the background and transfer data to python

rpy2 sets up some functions so that Python users can write and read some information in R. It is a lovely little package that simplifies a lot of things. But even if such a "bridge" is built, the process of calling R packages is more like "technically possible" rather than "it will be more convenient"

Unfortunately I couldn't get mgcv to work perfectly here, I'll explain later

<h3 style="text-align:center; color:blue;">Import rpy2</h3>

In [1]:
import rpy2
import rpy2.situation
for row in rpy2.situation.iter_info():
    print(row)
print(rpy2.__version__)

rpy2 version:
3.5.16
Python version:
3.12.4 (tags/v3.12.4:8e8a4ba, Jun  6 2024, 19:30:16) [MSC v.1940 64 bit (AMD64)]
Looking for R's HOME:
    Environment variable R_HOME: C:/PROGRA~1/R/R-43~1.1
    InstallPath in the registry: C:\Program Files\R\R-4.3.1
    Environment variable R_USER: None
    Environment variable R_LIBS_USER: None
R version:
    In the PATH: R version 4.3.1 (2023-06-16 ucrt) -- "Beagle Scouts"
    Loading R library from rpy2: OK
Additional directories to load R packages from:
None
C extension compilation:
  include:
  ['C:/PROGRA~1/R/R-43~1.1/include', 'C:/PROGRA~1/R/R-43~1.1/include/x64']
  libraries:
  ['R', 'm']
  library_dirs:
  ['C:/PROGRA~1/R/R-43~1.1/bin/x64']
  extra_compile_args:
  ['-std=c99']
  extra_link_args:
  []
Directory for the R shared library:
lib

CFFI extension type
  Environment variable: RPY2_CFFI_MODE
  Value: CFFI_MODE.ANY
  ABI: PRESENT
  API: ABSENT
3.5.16


In [2]:
import rpy2.robjects as robjects
from rpy2.robjects.packages import importr
from rpy2.robjects import pandas2ri
from rpy2.robjects.vectors import StrVector
from IPython.display import Image
from rpy2.robjects import r

These packages are necessary:

rpy2.robjects: Allows objects, functions, and data to be exchanged between Python and R.

importr: Import R extension packages in Python to expand Python's analysis and data processing capabilities.

pandas2ri: Conveniently convert data between pandas DataFrame and R dataframe.

StrVector: Allows string vector data to be transferred and manipulated between Python and R.

IPython.display.Image: Display image files in the IPython environment.

In [3]:
# import R packages
packnames = ('ggplot2', 'hexbin', 'lazyeval')
names_to_install = [x for x in packnames if not robjects.packages.isinstalled(x)]
if names_to_install:
    utils.install_packages(StrVector(names_to_install))

if not robjects.packages.isinstalled('devtools'):
    utils.install_packages(StrVector(['devtools']))

# import electBook 
devtools = importr('devtools')
devtools.install_github('mfasiolo/electBook')
electBook = importr('electBook')

R[write to console]: Skipping install of 'electBook' from a github remote, the SHA1 (38d7020f) has not changed since last install.
  Use `force = TRUE` to force installation



Now let’s import some R packages. Electbook contains our dataset, so we don’t need to download it from GitHub.

In [4]:
# Activate interaction between pandas and R
pandas2ri.activate()
# Load data and convert it to a pandas DataFrame
irish_agg = robjects.r('IrishAgg')  # Load 'IrishAgg' dataset from R
irish_agg_df = pandas2ri.rpy2py(irish_agg)  # Convert it to Pandas DataFrame

# Print the type of the DataFrame
print(type(irish_agg_df))

# Print the first few rows of the dataset
print(irish_agg_df.head())

<class 'pandas.core.frame.DataFrame'>
   time       toy  dow   holy  tod  temp                  dateTime       dem  \
1     1  0.986301    5  False  0.0   4.0 2009-12-29 23:00:00+00:00  1674.398   
2     2  0.986301    5  False  1.0   4.0 2009-12-29 23:30:00+00:00  1404.605   
3     3  0.986301    5  False  2.0   4.0 2009-12-30 00:00:00+00:00  1180.766   
4     4  0.986301    5  False  3.0   4.0 2009-12-30 00:30:00+00:00  1022.626   
5     5  0.986301    5  False  4.0   4.0 2009-12-30 01:00:00+00:00   877.018   

   dem48  temp95  
1    NaN     4.0  
2    NaN     4.0  
3    NaN     4.0  
4    NaN     4.0  
5    NaN     4.0  


Now that we have the dataset, pandas2ri converts the dataset to a python data frame. We can also do this in another example using the R reader.

In [5]:
from rpy2.robjects.packages import importr
mgcv=importr('mgcv')
#r['data']("IrishAgg")
formula = robjects.Formula('dem ~ dem48 + dow + s(temp) + s(temp95) + s(tod, bs="cc") + s(toy, bs="cc")')

# Define knots as an R list
knots = robjects.ListVector({
    'tod': robjects.IntVector([0, 48]),
    'toy': robjects.IntVector([0, 1])
})

# Fit the GAM model using gam function from mgcv package
fitIRI = mgcv.gam(formula, knots=knots, data=irish_agg_df)#data=robjects.globalenv['IrishAgg'])

# Print summary of the fitted model
print(robjects.r.summary(fitIRI))

c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\rpy2\robjects\pandas2ri.py:65: UserWarning: Error while trying to convert the column "dateTime". Fall back to string conversion. The error is: 'zoneinfo.ZoneInfo' object has no attribute 'zone'
  warnings.warn('Error while trying to convert '



Family: gaussian 
Link function: identity 

Formula:
dem ~ dem48 + dow + s(temp) + s(temp95) + s(tod, bs = "cc") + 
    s(toy, bs = "cc")

Parametric coefficients:
             Estimate Std. Error t value Pr(>|t|)    
(Intercept) 3.716e+02  7.995e+00  46.485  < 2e-16 ***
dem48       7.093e-01  5.422e-03 130.827  < 2e-16 ***
dow         3.869e+00  6.055e-01   6.391  1.7e-10 ***
---
Signif. codes:  0 '***' 0.001 '**' 0.01 '*' 0.05 '.' 0.1 ' ' 1

Approximate significance of smooth terms:
            edf Ref.df      F p-value    
s(temp)   8.595  8.945  31.93  <2e-16 ***
s(temp95) 8.587  8.953  11.22  <2e-16 ***
s(tod)    7.943  8.000 315.74  <2e-16 ***
s(toy)    7.588  8.000  32.65  <2e-16 ***
---
Signif. codes:  0 '***' 0.001 '**' 0.01 '*' 0.05 '.' 0.1 ' ' 1

R-sq.(adj) =  0.936   Deviance explained = 93.6%
GCV =  23193  Scale est. = 23144     n = 16751



We can see that the model fitIRI has been fitted. robjects.r.summary means that we run summary in R instead of Python, so we get the results output in R. If we try to summarize the model directly, it will not work because

In [6]:
type(fitIRI)

rpy2.robjects.vectors.ListVector

This model is of type rpy2.robjects.vectors.ListVector, which is a meaningless garbled string for Python's summary command. 
It would be interesting to try to make python understand the model output by R. I am not sure whether rpy2 can do this.

<h3 style="text-align:center; color:blue;">Some troubles</h3>
We know that everything is working reasonably well so far, but as we get deeper into using certain R-specific commands, things start to get complicated.


In [7]:
mgcViz = importr('mgcViz')

fitIRI_viz = mgcViz.getViz(fitIRI, nsim=50)

for element in fitIRI_viz:
    print(element)

[ 371.6394863     0.70933027    3.86926631  -31.56513202 -253.22777898
  -61.9862227  -205.19508945   43.48981814 -156.2358463    16.71832202
 -622.60476223  -59.14646661   -1.28798622  136.22254098   -8.48900228
 -135.81572926  -37.17546232   85.8178515    23.43346745  298.60615946
   43.05476655 -238.12590658 -249.97088691  -83.73100873   29.115402
   61.007688     79.79722916  255.62893947  211.36065646   -3.0607512
  -29.85821441  -58.04573579  -27.14047061  -24.73691488  -19.61585914
  -18.53413395    8.21065799]
[ 219.49814631  188.47277937  128.0996472  ... -230.05292666 -148.74422901
 -140.52455387]
[1636.45185369 1395.51522063 1175.5343528  ... 2220.16992666 2066.71022901
 1935.83155387]

Family: gaussian 
Link function: identity 


[1636.45185369 1395.51522063 1175.5343528  ... 2220.16992666 2066.71022901
 1935.83155387]
[3.8685423e+08]
[6.08406358e+09]
[1] 1

[1. 1. 1. ... 1. 1. 1.]
[1. 1. 1. ... 1. 1. 1.]
[1] 16750

[1855.95  1583.988 1303.634 ... 1990.117 1917.966 1795.307

We found some problems when executing the class command for fitIRI_viz. class() only works in the R environment, but the model is stored in the python environment. Calling rpy2 to return the result to python is not feasible because there is no fitIRI_viz data in the R environment.

In this way, we need to use RObjectMixin to call the R object, and then write a function to grab the ‘’class’’

In [8]:
# Import necessary modules
from rpy2.robjects import r, RObjectMixin

# Define a function to retrieve the class information of an object
def get_r_object_class(obj):
    return r('class')(obj)

# Get the class information of fitIRI_viz
fitIRI_viz_class = get_r_object_class(fitIRI_viz)

# Print the class information
print(fitIRI_viz_class)

['gamViz' 'gam' 'glm' 'lm']


We got what we wanted, but things got complicated

In [9]:
type(fitIRI_viz)

rpy2.robjects.vectors.ListVector

The data type is a collection of vectors

<h3 style="text-align:center; color:blue;">Plot by mgcViz</h3>
The rpy2 package defines some simple ways of drawing, such as the commonly used ggplot2 lattice, allowing some python statements to call them.

The mgcViz package does not seem to be included in this list. A common method is to directly run R statements. rpy2 provides the function of directly executing R statements (remember that R is always running in our background)



In [ ]:
r('''library(mgcv)
 fitIRI<-gam(dem~dem48+dow+s(temp)+s(temp95)+
 s(tod,bs="cc")+s(toy,bs="cc"),
 knots=list(tod=c(0,48),
 toy=c(0,1)),
 data=IrishAgg);
  library(mgcViz)
 fitIRI <- getViz(fitIRI, nsim = 50);
  ''')

I tried to combine the results of the check1D command directly into an image in the python environment, such as

check1D_result = mgcViz.check1D(fitIRI_viz, "dem48")

It works but the combined result cannot be recognized and plotted by Python. must run the R code directly to add them in the correct way.

Another problem is that I don’t know how to handle fitIRI_viz, which should be recognized by R statements but I haven’t succeeded yet, so as you can see in the cell above I refit the model in R to get fitIRI in the R environment

In [ ]:
#Running it works but there is no command to draw it
check1D_result = mgcViz.check1D(fitIRI_viz, "dem48")

Next, I will draw the graph. I am still trying to display the results directly in the notebook. The pdf file cannot be recognized and the png file does not seem to be successful. The image can actually be generated from R, but there are some problems if it is displayed through python.

In [ ]:
grdevices = importr('grDevices')
grdevices.pdf(file="myplot.pdf")

# Execute check1D on fitIRI with "dem48"
#check1D_result = mgcViz.check1D(fitIRI_viz, "dem48")

# Execute l_gridCheck1D with level = 0.95 and showReps = FALSE
#d = mgcViz.l_gridCheck1D(level=0.95, showReps=False)

robjects.r(  '''d<-(check1D(fitIRI, "dem48") + l_gridCheck1D(level = 0.95, showReps = FALSE)) ''')

plot_1 = robjects.r['d']

grdevices.dev_off()

print(plot_1)

In [ ]:
base = importr('base')
utils = importr('utils')
grdevices = importr('grDevices')

grdevices.pdf(file="myplot.pdf")

# Execute check1D on fitIRI with "dem48"
check1D_result = mgcViz.check1D(fitIRI_viz, "toy")

# Execute l_gridCheck1D with level = 0.95 and showReps = FALSE
#e = mgcViz.l_gridCheck1D(level=0.95, showReps=False)
robjects.r('''e<-(check1D(fitIRI, "toy") + l_gridCheck1D(level = 0.95, showReps = FALSE))''')

plot_2 = robjects.r['e']


grdevices.dev_off()

print(plot_2)

The above is a cumbersome but usable method (because the model needs to be refitted in R)

I guess the statement in check1D that directly adds the images is difficult to implement in a simple way. For example, we run the following code directly.

In [ ]:
plot1=mgcViz.check1D(fitIRI_viz, "dem48") + mgcViz.l_gridCheck1D(level = 0.95, showReps = False)
grdevices.dev_off()

print(plot1)

It actually works! But it doesn't draw the overlay image.

For the third image, the qq() command can be executed directly. Note that we are using fitIRI_viz, which is located in the python environment (corresponding to fitIRI in the R environment, they should be the same type of "thing")

In [ ]:
plot_3= mgcViz.qq(fitIRI_viz, method="tnormal", CI="normal", level=0.95)

grdevices.dev_off()

print(plot_3)

In [10]:
from rpy2.robjects.packages import importr
mgcv=importr('mgcv')
#r['data']("IrishAgg")
formula= robjects.Formula('dem ~ dow + s(dem48,k=10) + s(temp,k=20) + s(temp95,k=20) + s(tod,k=20,bs="cc") + s(toy,k=20)')

# Define knots as an R list
#knots = robjects.ListVector({
#    'tod': robjects.IntVector([0, 48]),
#    'toy': robjects.IntVector([0, 1])
#})

# Fit the GAM model using gam function from mgcv package
fitIRI2 = mgcv.gam(formula, knots=knots, data=irish_agg#robjects.globalenv['IrishAgg']
                   , family='scat', aGam=robjects.ListVector({'knots': knots}), aViz=robjects.ListVector({'nsim': 50}))

# Print summary of the fitted model
print(r.summary(fitIRI2))


Family: Scaled t(3,76.068) 
Link function: identity 

Formula:
dem ~ dow + s(dem48, k = 10) + s(temp, k = 20) + s(temp95, k = 20) + 
    s(tod, k = 20, bs = "cc") + s(toy, k = 20)

Parametric coefficients:
            Estimate Std. Error z value Pr(>|z|)    
(Intercept) 1350.754      2.037 662.995   <2e-16 ***
dowThu       -34.965      2.809 -12.446   <2e-16 ***
dowMon       -23.627      2.775  -8.514   <2e-16 ***
dowTue       -23.948      2.801  -8.551   <2e-16 ***
dowWed       -30.800      2.796 -11.015   <2e-16 ***
dowSat        43.314      2.848  15.207   <2e-16 ***
dowFri       -29.396      2.856 -10.292   <2e-16 ***
---
Signif. codes:  0 '***' 0.001 '**' 0.01 '*' 0.05 '.' 0.1 ' ' 1

Approximate significance of smooth terms:
             edf Ref.df  Chi.sq p-value    
s(dem48)   8.415  8.909 60963.2  <2e-16 ***
s(temp)   11.127 13.392   141.0  <2e-16 ***
s(temp95)  9.007 11.218   211.9  <2e-16 ***
s(tod)    17.451 18.000  2349.2  <2e-16 ***
s(toy)     9.153 11.304   219.8  <2e-16

Here we fit a second model, but for the same reason, this model is difficult to understand and plot using Python, so we will use R again to fit the model.

In [ ]:
robjects.r(''' fitIRI_2<-gamV(dem~dow+s(dem48,k=10)+
 s(temp,k=20)+s(temp95,k=20)+
 s(tod,k=20,bs="cc")+s(toy,k=20),
 data=IrishAgg,
 family= scat,
 aGam=list(knots= list(tod= c(0,48))),
 aViz=list(nsim=50))''')

In [ ]:
r(''' g<-AIC(fitIRI,fitIRI_2)
 f<-check(fitIRI_2)''')
plot_3 = robjects.r['f']
print(plot_3)
AIC = robjects.r['g']
print(AIC)

Looking at the AIC, it is the same as that obtained by R language. From this, it seems that running the R command directly can get the required results

In [ ]:
r('''print(plot(fitIRI_2,allTerms=TRUE),pages=1,
 layout_matrix=matrix(1:6,3,2))''')

In general, we successfully displayed the required files. Although there were many difficulties, it was achievable to a certain extent. However, the data formats generated by the two languages ​​are not the same and in most cases there is no effective "translation". Many additional functions need to be defined to make the data read from each other.

And I didn’t run the part that generates the image, otherwise the notebook file would be too large